In [10]:
# Qiskit packages
import qiskit, qiskit_aer#, qiskit_ibm_runtime, qiskit_ibm_catalog, qiskit_serverless   

import sys, os, pathlib
# starting from the notebook folder
nb_dir = pathlib.Path.cwd()
# go up to the parent folder that contains BOTH notebook_files/ and python_files/
project_root = nb_dir.parent
# put that folder on sys.path (so "python_files" becomes importable)
sys.path.insert(0, str(project_root))

# Own packages
import python_files.Query as qry
import python_files.RS_prep as rsp
import python_files.General as grl
import python_files.Stabilizer_and_Graphs as sg

# Other packages
import numpy as np 
import math
import time
import matplotlib.pyplot as plt

In [11]:
# Qiskit functions
from qiskit import QuantumRegister, ClassicalRegister, QuantumCircuit, transpile
from qiskit.quantum_info import Statevector, Clifford, Pauli, PauliList
from qiskit.circuit import Instruction
from qiskit.circuit.classical import expr
from qiskit_aer import AerSimulator
from qiskit.transpiler.passes import RemoveBarriers
from qiskit.transpiler import CouplingMap

# Other funtions
from typing import Optional
from __future__ import annotations
from IPython.display import Math
from numpy.random import default_rng
from collections import deque, Counter

In [24]:
n = 2
N = 2**n

num_qubits = 3*N-2   # N-1 d_nohe qubits and 2N-1 dprime qubits
outcomes = grl.all_binary_lists(num_qubits)
outcome = outcomes[30]
print(outcome)

P_in = outcome_string_to_Pin(outcome, n)

print(P_in.x)
print(P_in.z)

[0, 1, 1, 1, 1, 0, 0, 0, 0, 0]
[False  True  True False False False False]
[ True  True False False False False False]


In [9]:
def bits_to_int(lsb_first):
    return sum(b << i for i, b in enumerate(lsb_first))

    
def all_binary_lists(n: int):
    """Return 2^n lists (length n) with first position flipping fastest."""
    return [list(bits)[::-1] for bits in product([0, 1], repeat=n)]

In [10]:
print(bits_to_int([0, 0, 1]))

4


In [39]:
n = 1
N = 2**n

num_qubits = 3*N-2   # N-1 d_nohe qubits and 2N-1 dprime qubits
outcomes = grl.all_binary_lists(num_qubits) 
d_Pouts  = precompute_merge_corrections(n)

for outcome, key in zip(outcomes, d_Pouts):
    print(f"outcome arr: {outcome}")
    P_in = outcome_string_to_Pin(outcome, n)
    print(f"P_in x: {P_in.x}")
    print(f"P_in z: {P_in.z}")
    P_out = d_Pouts[key]
    print(f"P_out x: {P_out.x}")
    print(f"P_out z: {P_out.z}")

outcome arr: [0, 0, 0, 0]
P_in x: [False False False False False]
P_in z: [False False False False False]
P_out x: [False False False False False]
P_out z: [False False False False False]
outcome arr: [1, 0, 0, 0]
P_in x: [ True False False False False]
P_in z: [False False False False False]
P_out x: [ True False False False False]
P_out z: [False False False  True False]
outcome arr: [0, 1, 0, 0]
P_in x: [False False False False False]
P_in z: [ True False False False False]
P_out x: [False False False False False]
P_out z: [ True False False False False]
outcome arr: [1, 1, 0, 0]
P_in x: [ True False False False False]
P_in z: [ True False False False False]
P_out x: [ True False False False False]
P_out z: [ True False False  True False]
outcome arr: [0, 0, 1, 0]
P_in x: [False False False False False]
P_in z: [False  True False False False]
P_out x: [False False False False False]
P_out z: [False  True  True False False]
outcome arr: [1, 0, 1, 0]
P_in x: [ True False False False F

In [50]:
def merge_phi1_phi2_normal(qc1, qc2, n, third_wires):
    """
    """

    def outcome_string_to_Pin(outcome, n):
        N = 2**n
        num_A2_qubits = 2*(2*N-n-2)
    
        # separate d_nohe values from dpime values
        d_nohe_outcomes = outcome[:N-1]
        dprime_outcomes = outcome[N-1:]
    
        # make P_in
        x = np.array(d_nohe_outcomes + N*[0] + num_A2_qubits*[0], dtype=bool)
        z = np.array(dprime_outcomes + num_A2_qubits*[0], dtype=bool)  
        P_in = Pauli((z, x))
    
        return P_in
    
    def precompute_merge_corrections(n):
        N = 2**n
    
        num_d_nohe_qubits = N-1
        num_dprime_qubits = 2*N-1
        num_qubits        = num_d_nohe_qubits + num_dprime_qubits
        
        all_outcomes = grl.all_binary_lists(num_qubits)
    
        C = Clifford(rsp.make_C_NOHE_circuit(n+1 , measure=False)[0])  # note n+1 instead of n
        d = {}
    
        for outcome in all_outcomes:
            P_in = outcome_string_to_Pin(outcome, n)
            P_out = P_in.evolve(C, frame="s")
            d[grl.bits_to_int(outcome)] = P_out
    
        return d
        
    N = 2**n
    
    # tensor phi1 and phi2
    qc = qc2.tensor(qc1)
    
    # apply CZs between D_NOHE + L and Dprime
    D_NOHE, L, Dprime = grl.get_qreg(qc, "D_NOHE"), grl.get_qreg(qc, "L"), grl.get_qreg(qc, "Dprime")
    qc.cz(D_NOHE[:] + L[:], Dprime[:])
    
    # add cregs for D_NOHE and Dprime, then measure in X basis
    merge_clr = ClassicalRegister(3*N-2, "merge_clr")
    qc.add_register(merge_clr)
    
    qc.h(D_NOHE[:] + Dprime[:])
    qc.measure(D_NOHE[:] + Dprime[:], merge_clr[:])

    # precompute pauli corrections
    P_out_dict = precompute_merge_corrections(n)

    # rotate q2's in K2 back to Z frame before applying corrections
    for q2 in third_wires:
        qc.h(q2)

    # apply pauli corrections
    K2 = grl.get_qreg(qc, "K2")
    A2 = grl.get_qreg(qc, "A2")
    for outcome, P_out in P_out_dict.items():
        with qc.if_test((merge_clr, outcome)):
            Zarr, Xarr = P_out.z, P_out.x
            j = 0
            for q in (K2[:] + A2[:]):
                if Zarr[j]:
                    qc.z(q)
                if Xarr[j]:
                    qc.x(q)
                j += 1

    # measure q2's in K2 in X basis
    K2_clr = grl.get_creg(qc, "K2_clr")
    j = 0
    for q2 in third_wires:
        qc.h(q2)
        qc.measure(q2, K2_clr[j])
        j += 1

    return qc

def make_phi_normal(n):
    qc1 = rsp.make_Phi1(n)
    qc2, K2, A2, K2_clr, mapping, info, third_wires = rsp.make_Phi2(n)
    
    qc = merge_phi1_phi2(qc1, qc2, n, third_wires)

    return qc
    

In [4]:
n = 2

qc = rsp.make_phi_normal(n)

grl.print_qubit_table(qc)
qc.draw("mpl", scale=0.7)

qubit                                    global  register  reg_idx
------------------------------------------------------------------
<Qubit register=(2, "I"), index=0>            0  I               0
<Qubit register=(2, "I"), index=1>            1  I               1
<Qubit register=(3, "D_NOHE"), index=0>       2  D_NOHE          0
<Qubit register=(3, "D_NOHE"), index=1>       3  D_NOHE          1
<Qubit register=(3, "D_NOHE"), index=2>       4  D_NOHE          2
<Qubit register=(4, "L"), index=0>            5  L               0
<Qubit register=(4, "L"), index=1>            6  L               1
<Qubit register=(4, "L"), index=2>            7  L               2
<Qubit register=(4, "L"), index=3>            8  L               3
<Qubit register=(7, "Dprime"), index=0>       9  Dprime          0
<Qubit register=(7, "Dprime"), index=1>      10  Dprime          1
<Qubit register=(7, "Dprime"), index=2>      11  Dprime          2
<Qubit register=(7, "Dprime"), index=3>      12  Dprime       

In [42]:
# USING MERGED PHI's (v2) - This test only works when you do not entangle L with D'. But, I'm not sure whether it actually tests the merging in that case.
n = 1
N = 2**n

addr = 0
vec = np.zeros([N])
vec[addr] = 1
qc_addr = qry.initialize_adresses(n, register_name="R", method="Supply vector", vec=vec)
qc_RS = make_phi(n)
qc = qc_RS.tensor(qc_addr)

# qc.save_statevector("after RS prep", pershot=True)

qry.query_step_i(qc, n)

# rotate '+' qubit in OHE state to -1 in Z-basis
L = grl.get_qreg(qc, "L")
I_clr = grl.get_creg(qc, "I_clr")
for b in range(N):
    with qc.if_test((I_clr, b)):
        p = addr ^ b
        qc.z(L[p])
        qc.h(L[p])

L_clr = grl.get_creg(qc, "L_clr")
qc.measure(L, L_clr)

In [43]:
shots=50
# simulate
sim = AerSimulator(method= "statevector")
tqc = transpile(qc, backend=sim, optimization_level=0)
res = sim.run(tqc, shots=shots, memory=True).result()

print("Success:", res.success)
print("Overall status:", res.to_dict().get("status", ""))

mem    = res.get_memory()
counts = res.get_counts()

grl.print_qubit_table(qc)

for m in mem:
    print(m)

Success: True
Overall status: COMPLETED
qubit                                    global  register  reg_idx
------------------------------------------------------------------
<Qubit register=(1, "R"), index=0>            0  R               0
<Qubit register=(1, "I"), index=0>            1  I               0
<Qubit register=(1, "D_NOHE"), index=0>       2  D_NOHE          0
<Qubit register=(2, "L"), index=0>            3  L               0
<Qubit register=(2, "L"), index=1>            4  L               1
<Qubit register=(3, "Dprime"), index=0>       5  Dprime          0
<Qubit register=(3, "Dprime"), index=1>       6  Dprime          1
<Qubit register=(3, "Dprime"), index=2>       7  Dprime          2
<Qubit register=(3, "K2"), index=0>           8  K2              0
<Qubit register=(3, "K2"), index=1>           9  K2              1
<Qubit register=(3, "K2"), index=2>          10  K2              2
<Qubit register=(2, "A2"), index=0>          11  A2              0
<Qubit register=(2, "A